In [1]:
import pandas as pd
import gensim
import re
import logging
import random
import pickle as pkl
import numpy as np
from tqdm import tqdm

logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [2]:
out_data=pd.read_csv('data_by_cj/vid.csv',index_col=0)
print(out_data.last_valid_index())

13262


In [3]:
vids=pd.DataFrame(out_data['video_id'])
titles=pd.DataFrame(out_data['title'])

In [17]:
vids

video_id
0      ZBTPLVePE7M
1      aRM3hYrs8vc
2      g7wcHPE8py4
3      HmphRR9IdOk
4      nUPm-loO4FE
...            ...
13258  uIBXibRfy6Y
13259  dD0mk2_lvXI
13260  VL52mhOyRLA
13261  HimdQI73Vr0
13262  -wk-sGhed8U

[13263 rows x 1 columns]

In [4]:
vids.describe()

video_id
count         13263
unique        13263
top     ZBTPLVePE7M
freq              1

In [5]:
titles.describe()

title
count                                               13263
unique                                              13031
top     ASMR MUKBANG NOODLES, SPICY SEAFOOD, 불닭 팽이버섯 먹...
freq                                                   20

In [6]:
def titles2corpus(titles, isTrain):
    for i, title in titles.iterrows():
        title=title.item()
        tokens=gensim.utils.simple_preprocess(title)
        parsed=[]    
        for word in tokens:
            word=word.replace('ㅣ'," ")
            temp=word.split(' ')
            for t in temp:
                if not t=="":
                    parsed.append(t)
        if isTrain:
            yield gensim.models.doc2vec.TaggedDocument(parsed,[i])
        else:
            yield parsed

train_corpus=list(titles2corpus(titles,True))


In [7]:
doc2vec_model=gensim.models.doc2vec.Doc2Vec(vector_size=10, min_count=1, epochs=10000, max_vocab_size=None, window=10)

2023-05-12 21:52:34,405 : INFO : Doc2Vec lifecycle event {'params': 'Doc2Vec(dm/m,d10,n5,w10,s0.001,t3)', 'datetime': '2023-05-12T21:52:34.405510', 'gensim': '4.1.2', 'python': '3.9.12 (main, Apr  4 2022, 05:22:27) [MSC v.1916 64 bit (AMD64)]', 'platform': 'Windows-10-10.0.19044-SP0', 'event': 'created'}


In [8]:
doc2vec_model.build_vocab(train_corpus)

2023-05-12 21:52:34,445 : INFO : collecting all words and their counts
2023-05-12 21:52:34,446 : INFO : PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2023-05-12 21:52:34,472 : INFO : PROGRESS: at example #10000, processed 105885 words (4074662/s), 26023 word types, 0 tags
2023-05-12 21:52:34,484 : INFO : collected 32056 word types and 13263 unique tags from a corpus of 13263 examples and 138423 words
2023-05-12 21:52:34,499 : INFO : Creating a fresh vocabulary
2023-05-12 21:52:34,583 : INFO : Doc2Vec lifecycle event {'msg': 'effective_min_count=1 retains 32056 unique words (100.0%% of original 32056, drops 0)', 'datetime': '2023-05-12T21:52:34.583424', 'gensim': '4.1.2', 'python': '3.9.12 (main, Apr  4 2022, 05:22:27) [MSC v.1916 64 bit (AMD64)]', 'platform': 'Windows-10-10.0.19044-SP0', 'event': 'prepare_vocab'}
2023-05-12 21:52:34,583 : INFO : Doc2Vec lifecycle event {'msg': 'effective_min_count=1 leaves 138423 word corpus (100.0%% of original 138423, drops 0

In [9]:
print(f"Word '먹방' appeared {doc2vec_model.wv.get_vecattr('먹방', 'count')} times in the training corpus.")
print(f"Word 'mukbang' appeared {doc2vec_model.wv.get_vecattr('mukbang', 'count')} times in the training corpus.")

Word '먹방' appeared 3064 times in the training corpus.
Word 'mukbang' appeared 5176 times in the training corpus.


In [10]:
doc2vec_model.train(train_corpus, total_examples=doc2vec_model.corpus_count, epochs=doc2vec_model.epochs)

2023-05-12 21:52:35,044 : INFO : Doc2Vec lifecycle event {'msg': 'training model with 3 workers on 32056 vocabulary and 10 features, using sg=0 hs=0 sample=0.001 negative=5 window=10 shrink_windows=True', 'datetime': '2023-05-12T21:52:35.044521', 'gensim': '4.1.2', 'python': '3.9.12 (main, Apr  4 2022, 05:22:27) [MSC v.1916 64 bit (AMD64)]', 'platform': 'Windows-10-10.0.19044-SP0', 'event': 'train'}
2023-05-12 21:52:35,594 : INFO : worker thread finished; awaiting finish of 2 more threads
2023-05-12 21:52:35,640 : INFO : worker thread finished; awaiting finish of 1 more threads
2023-05-12 21:52:35,647 : INFO : worker thread finished; awaiting finish of 0 more threads
2023-05-12 21:52:35,648 : INFO : EPOCH - 1 : training on 138423 raw words (136877 effective words) took 0.6s, 230109 effective words/s
2023-05-12 21:52:36,182 : INFO : worker thread finished; awaiting finish of 2 more threads
2023-05-12 21:52:36,209 : INFO : worker thread finished; awaiting finish of 1 more threads
2023-05

In [11]:

for i in range(10):
    doc_id = random.randint(0, len(train_corpus) - 1)
    inferred_vector = doc2vec_model.infer_vector(train_corpus[doc_id].words)
    sims = doc2vec_model.dv.most_similar([inferred_vector], topn=4)

    # Compare and print the most/median/least similar documents from the train corpus
    print('Test Document ({}): «{}»'.format(doc_id, ' '.join(train_corpus[doc_id].words)))
    print(u'SIMILAR DOCS PER MODEL %s:' % doc2vec_model)
    for label, index in [('MOST1', 1),('MOST2', 2), ('MOST3', 3)]:
        print(u'%s: %s, similarity:%s: «%s»' % (label, sims[index][0], sims[index][1], ' '.join(train_corpus[sims[index][0]].words)))
    print()

Test Document (10453): «dow jones latest news dow jones latest update shorts trending viral share dow jones»
SIMILAR DOCS PER MODEL Doc2Vec(dm/m,d10,n5,w10,s0.001,t3):
MOST1: 7548, similarity:0.9541876912117004: «banana chocolate chip muffins»
MOST2: 10450, similarity:0.948101282119751: «dow jones latest news nifty news nasdaq news nifty bank news shorts trending viral»
MOST3: 10449, similarity:0.9474686980247498: «nifty latest news nifty crash news shorts viral share stockmarket»

Test Document (6605): «blacforest kukus telur untuk bascake ala sweet_cake»
SIMILAR DOCS PER MODEL Doc2Vec(dm/m,d10,n5,w10,s0.001,t3):
MOST1: 7922, similarity:0.9479679465293884: «resep anak kost kaum mager masak sakarepmu shorts bandungpisan ngeshortsbareng»
MOST2: 8916, similarity:0.9440456032752991: «besan ka chila banaye recipe dailyrecipie trending recipeoftheday besankachilla chilla shorts»
MOST3: 13178, similarity:0.9408147931098938: «влог месяц герману пасха готовка рецепт прогулка семья любовь дети»

In [14]:
out_vec=np.empty((0,11),dtype=object)
for i in tqdm(range(len(train_corpus))):
    vec=doc2vec_model.__getitem__(i)
    temp=np.array(vec,dtype=object)
    temp=np.insert(temp,0,vids.loc[i].item()).reshape((1,11))
    out_vec=np.append(out_vec,temp,axis=0)

100%|██████████| 13263/13263 [00:04<00:00, 2920.53it/s]


In [15]:
with open('title_doc2vec_10','wb') as f:
    pkl.dump(out_vec,f)

In [16]:
check=""
with open('title_doc2vec_10','rb') as f:
    check=pkl.load(f)
check

array([['ZBTPLVePE7M', -0.04810052737593651, -0.0759095773100853, ...,
        0.03384330868721008, 0.008915675804018974, 0.12357833236455917],
       ['aRM3hYrs8vc', 0.01553319487720728, 0.004712170455604792, ...,
        0.05644267052412033, 0.16613872349262238, 0.028923319652676582],
       ['g7wcHPE8py4', 0.07173019647598267, 0.1367124319076538, ...,
        -0.046646084636449814, 0.17967595160007477, -0.05262669548392296],
       ...,
       ['VL52mhOyRLA', 3.6532981395721436, 6.814709663391113, ...,
        5.048295974731445, -2.04594349861145, -4.639875411987305],
       ['HimdQI73Vr0', 1.3339227437973022, -1.2944780588150024, ...,
        -4.118017673492432, 1.3564026355743408, -1.117978811264038],
       ['-wk-sGhed8U', 0.11791582405567169, -3.7393221855163574, ...,
        -3.9922780990600586, 1.0680451393127441, -3.947176694869995]],
      dtype=object)